In [42]:
import sys
sys.path.append("/home/azhuavlev/PycharmProjects/ml-neuman_mano")

%load_ext autoreload
%autoreload 2

import lighning_models
import lightning as L
from lightning.pytorch.loggers import TensorBoardLogger
import nerf
import dataset_canonical_space
from torch.utils.data import DataLoader
import dataset_from_files
import glob
import os
import glob
import json
import math
import matplotlib.pyplot as plt
import numpy as np
import os
import pytorch3d
import sys
import time
import torch
from IPython import display
from PIL import Image
from pytorch3d.renderer import (
    FoVPerspectiveCameras,
    NDCMultinomialRaysampler,
    MonteCarloRaysampler,
    EmissionAbsorptionRaymarcher,
    ImplicitRenderer,
    RayBundle,
    ray_bundle_to_ray_points,
)
# Data structures and functions for rendering
from pytorch3d.structures import Volumes
from pytorch3d.transforms import so3_exp_map
from tqdm import tqdm

from generate_cow_renders import generate_cow_renders
from plot_image_grid import image_grid

from helpers import *
from nerf import *
import nerf_original

from data_io import neuman_helper

device = 'cuda' if torch.cuda.is_available() else 'cpu'

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [43]:
# disable pytorch gradient computation
torch.set_grad_enabled(False)

data_path = '/home/azhuavlev/Desktop/Data/InterHand_Neuman/03'
all_ids = list(range(len(glob.glob(os.path.join(data_path, 'cameras', '*.json')))))

# use 80% of the data for training, randomize the order
np.random.shuffle(all_ids)
train_ids = all_ids[:int(0.6 * len(all_ids))]
test_ids = all_ids[int(0.6 * len(all_ids)):]
print(test_ids)

train_dataset = dataset_from_files.NeumanDataset(data_path, train_ids)
test_dataset = dataset_from_files.NeumanDataset(data_path, test_ids)
full_dataset = dataset_from_files.NeumanDataset(data_path, all_ids)

# We sample 6 random cameras in a minibatch.
batch_size = 1

train_loader = DataLoader(train_dataset, batch_size=batch_size, shuffle=True, num_workers=5)
test_loader = DataLoader(test_dataset, batch_size=batch_size, shuffle=False)
full_loader = DataLoader(full_dataset, batch_size=batch_size, shuffle=False)

field = nerf_original.NeuralRadianceField()

ckpt_path = '/home/azhuavlev/Desktop/Results/neuman_custom/lightning_logs/version_148/checkpoints/epoch=1199-step=57600.ckpt'
model = lighning_models.HandModel(dataset=full_loader, nerf_model=field).load_from_checkpoint(ckpt_path,
                                                                                             dataset=full_loader,
                                                                                             nerf_model=field)

model = model.to('cuda')

[9, 16, 19, 44, 45, 6, 17, 12, 50, 32, 2, 24, 7, 31, 58, 56, 22, 13, 51, 54, 41, 4, 59, 39]
min_depth tensor(0.7476)
max_depth tensor(1.5189)
render_size_x 512
render_size_y 334
min_depth tensor(0.7476)
max_depth tensor(1.5189)
render_size_x 512
render_size_y 334


In [44]:
# generate points in 3d space between -0.3 and 0.3
with torch.no_grad():
    point_cloud = torch.linspace(-0.1, 0.2, 200, device='cpu')
    points = torch.stack(torch.meshgrid(point_cloud, point_cloud, point_cloud), dim=-1).reshape(1, 1, -1, 1, 3)
    directions = torch.zeros(1, 1, points.shape[2], 3, device = points.device)
print('points', points.shape)
print('directions', directions.shape)

points torch.Size([1, 1, 8000000, 1, 3])
directions torch.Size([1, 1, 8000000, 3])


In [45]:
from tqdm import tqdm
# iterate over points in chunks of 1000000:
rays_densities = torch.tensor([], device='cpu')
rays_colors = torch.tensor([], device='cpu')

with torch.no_grad():
    for i in tqdm(range(0, points.shape[2], 1000000)):
        points_batch = points[:, :, i:i+1000000,:,  :].to('cuda')
        directions_batch = directions[:, :, i:i+1000000, :].to('cuda')
        rays_densities_batch, rays_colors_batch = model.get_nerf_output(points_batch, directions_batch)

        rays_densities = torch.cat((rays_densities, rays_densities_batch.cpu()), dim=2)
        rays_colors = torch.cat((rays_colors, rays_colors_batch.cpu()), dim=2)

  0%|                                                                                                                                                               | 0/8 [00:00<?, ?it/s]


AttributeError: 'NeuralRadianceField' object has no attribute 'harmonic_embedding'

In [5]:
rays_densities_xyz = rays_densities.reshape(200, 200, 200)

In [6]:
print('fraction occupied > 0.1', np.mean(rays_densities.cpu().numpy() > 0.1))
print('fraction occupied > 0.9', np.mean(rays_densities.cpu().numpy() > 0.9))

fraction occupied > 0.1 0.007346375
fraction occupied > 0.9 0.00132775


In [41]:
import numpy as np
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d.art3d import Poly3DCollection

from skimage import measure
from skimage.draw import ellipsoid
import trimesh

verts, faces, normals, values = measure.marching_cubes(rays_densities_xyz.cpu().numpy(), 0.1)
mesh = trimesh.Trimesh(vertices=verts, faces=faces)

# display mesh
mesh.show()

In [20]:
verts

array([[ 47.86058, 120.     , 108.     ],
       [ 48.     , 120.     , 107.84547],
       [ 48.     , 119.81754, 108.     ],
       ...,
       [154.5987 ,  99.     , 116.     ],
       [154.56816,  99.     , 119.     ],
       [154.49202, 100.     , 112.     ]], dtype=float32)

In [40]:

# save mesh as obj
# mesh.export('mesh.obj')

In [21]:
# print max and min of verts
for i in range(3):
    print(np.min(verts[:, i]) / 100 * 0.6 + -0.3, np.max(verts[:, i]) / 100 * 0.6 + -0.3)

for i in range(3):
    print(np.min(verts[:, i]), np.max(verts[:, i]))

-0.012836517333984387 0.6275921630859376
0.029018920898437495 0.8341935424804685
0.1865571899414062 0.6709487915039063
47.86058 154.5987
54.836487 189.03226
81.092865 161.8248


In [9]:
torch.cuda.empty_cache()

In [10]:
!nvidia-smi

Sun Jul  9 14:32:24 2023       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 470.141.03   Driver Version: 470.141.03   CUDA Version: 11.4     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  NVIDIA GeForce ...  On   | 00000000:05:00.0 Off |                  N/A |
| 22%   52C    P2    84W / 250W |   1241MiB / 12212MiB |     68%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

In [11]:
import skimage

In [12]:
import numpy as np
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d.art3d import Poly3DCollection

from skimage import measure
from skimage.draw import ellipsoid


# Generate a level set about zero of two identical ellipsoids in 3D
ellip_base = ellipsoid(6, 10, 16, levelset=True)
ellip_double = np.concatenate((ellip_base[:-1, ...],
                               ellip_base[2:, ...]), axis=0)

# Use marching cubes to obtain the surface mesh of these ellipsoids
verts, faces, normals, values = measure.marching_cubes(ellip_double, 0)

In [13]:
print(ellip_double.shape)
ellip_double

(27, 23, 35)


array([[[2.70001736, 2.57111111, 2.45001736, ..., 2.45001736,
         2.57111111, 2.70001736],
        [2.49001736, 2.36111111, 2.24001736, ..., 2.24001736,
         2.36111111, 2.49001736],
        [2.30001736, 2.17111111, 2.05001736, ..., 2.05001736,
         2.17111111, 2.30001736],
        ...,
        [2.30001736, 2.17111111, 2.05001736, ..., 2.05001736,
         2.17111111, 2.30001736],
        [2.49001736, 2.36111111, 2.24001736, ..., 2.24001736,
         2.36111111, 2.49001736],
        [2.70001736, 2.57111111, 2.45001736, ..., 2.45001736,
         2.57111111, 2.70001736]],

       [[2.33890625, 2.21      , 2.08890625, ..., 2.08890625,
         2.21      , 2.33890625],
        [2.12890625, 2.        , 1.87890625, ..., 1.87890625,
         2.        , 2.12890625],
        [1.93890625, 1.81      , 1.68890625, ..., 1.68890625,
         1.81      , 1.93890625],
        ...,
        [1.93890625, 1.81      , 1.68890625, ..., 1.68890625,
         1.81      , 1.93890625],
        [2.1

In [14]:
# Display resulting triangular mesh using Matplotlib. This can also be done
# with mayavi (see skimage.measure.marching_cubes docstring).
fig = plt.figure()
ax = fig.add_subplot(111, projection='3d')

# Fancy indexing: `verts[faces]` to generate a collection of triangles
mesh = Poly3DCollection(verts[faces])
mesh.set_edgecolor('k')
ax.add_collection3d(mesh)

ax.set_xlabel("x-axis: a = 6 per ellipsoid")
ax.set_ylabel("y-axis: b = 10")
ax.set_zlabel("z-axis: c = 16")

ax.set_xlim(0, 24)  # a = 6 (times two for 2nd ellipsoid)
ax.set_ylim(0, 20)  # b = 10
ax.set_zlim(0, 32)  # c = 16

plt.tight_layout()
plt.show()

<IPython.core.display.Javascript object>